# ERA5 EVAP from AWS:  Virtualizarr & Icechunk

In [1]:
import warnings
warnings.filterwarnings("ignore", category=UserWarning)

In [2]:
import icechunk

In [3]:
import xarray as xr
from obstore.store import from_url

from virtualizarr import open_virtual_dataset
from virtualizarr.parsers import HDFParser
from virtualizarr.registry import ObjectStoreRegistry

In [4]:
data_bucket = "s3://nsf-ncar-era5"

In [5]:
import os
from dotenv import load_dotenv
_ = load_dotenv(f'{os.environ['HOME']}/dotenv/rsignell4.env')

# Define Icechunk storage
storage_endpoint = 'https://pangeo-eosc-minioapi.vm.fedcloud.eu'
storage_bucket = 'rsignell4-protocoast'
storage_name = 'era5-evap-icechunk'

In [6]:
storage = icechunk.s3_storage(
    bucket=storage_bucket,
    prefix=f"icechunk/{storage_name}",
    from_env=True,
    endpoint_url=storage_endpoint,
    region='not-used',   # N/A for Pangeo-EOSC bucket, but required param
    force_path_style=True)

In [7]:
config = icechunk.RepositoryConfig.default()
config.set_virtual_chunk_container(
    icechunk.VirtualChunkContainer(
        url_prefix=f"{data_bucket}/",
        store=icechunk.s3_store(region="us-west-2", anonymous=True, s3_compatible=True, 
                                force_path_style=True),
    ),
)

In [8]:
import fsspec
fs = fsspec.filesystem('s3', anon=True)
fs_write = fsspec.filesystem('s3', anon=False, endpoint_url=storage_endpoint)

In [9]:
mon_list = fs.ls(f'{data_bucket}/e5.oper.fc.sfc.accumu/')[1:]

In [10]:
print(mon_list[0])
print(mon_list[-1])

nsf-ncar-era5/e5.oper.fc.sfc.accumu/194001
nsf-ncar-era5/e5.oper.fc.sfc.accumu/202506


In [11]:
store = from_url(data_bucket, region="us-west-2", skip_signature=True)
registry = ObjectStoreRegistry({data_bucket: store})
parser = HDFParser()

In [12]:
credentials = icechunk.containers_credentials({f"s3://{data_bucket}/": icechunk.s3_credentials(anonymous=True)})

In [13]:
def fix_ds(ds):
    return ds.drop_vars(['utc_date'])    # <<= This 'utc_date' was making xr.concat bomb out, so we drop it

In [14]:
def create_or_append(flist, create=False):
    flist = [f's3://{f}' for f in flist]
    if create:
        # remove old existing icechunk storage with this name
        try:
            # Use the same prefix as the storage
            fs_write.rm(f's3://{storage_bucket}/icechunk/{storage_name}', recursive=True)
            print('removing old icechunk storage')
        except:
            pass

    ds_list = [
        open_virtual_dataset(
            url=f,
            parser=parser,
            registry=registry, 
            loadable_variables=["forecast_initial_time"]) for f in flist]

    ds_list = [fix_ds(ds) for ds in ds_list]

    ds = xr.concat(
        ds_list,
        dim="forecast_initial_time",
        coords="minimal",
        compat="override",
        combine_attrs="override",
    )
    if create:
        repo = icechunk.Repository.create(storage, config)
        session = repo.writable_session("main")
        ds.virtualize.to_icechunk(session.store)
        session.commit("Initial ERA5 Evap creation")
    else:
        repo = icechunk.Repository.open(storage, config, authorize_virtual_chunk_access=credentials)
        append_session = repo.writable_session("main")
        ds.virtualize.to_icechunk(append_session.store, append_dim="forecast_initial_time")
        append_session.commit("Append more ERA5 Evap Files")

## Create the icechunk using mon_list[0]

In [15]:
flist = fs.glob(f'{mon_list[0]}/*128_182_e*.nc')
create_or_append(flist, create=True)

['nsf-ncar-era5/e5.oper.fc.sfc.accumu/194001/e5.oper.fc.sfc.accumu.128_182_e.ll025sc.1940010106_1940011606.nc',
 'nsf-ncar-era5/e5.oper.fc.sfc.accumu/194001/e5.oper.fc.sfc.accumu.128_182_e.ll025sc.1940011606_1940020106.nc']

## Append all the other months

In [ ]:
%%time
for mon in mon_list[1:]:  # <== starting at mon_list[1] because we used mon_list[0] to create
    print(mon)
    flist = fs.glob(f'{mon}/*128_182_e*.nc')
    create_or_append(flist, create=False)

## Check that it worked

In [18]:
credentials = icechunk.containers_credentials(
    {f"{data_bucket}/": icechunk.s3_credentials(anonymous=True)})

read_repo = icechunk.Repository.open(
    storage, config, authorize_virtual_chunk_access=credentials)

read_session = read_repo.readonly_session("main")

ds = xr.open_zarr(read_session.store, consolidated=False, zarr_format=3, chunks={'forecast_initial_time':5})

ds

<xarray.Dataset> Size: 9GB
Dimensions:                (forecast_initial_time: 182, forecast_hour: 12,
                            latitude: 721, longitude: 1440)
Coordinates:
  * forecast_initial_time  (forecast_initial_time) datetime64[ns] 1kB 1940-01...
  * forecast_hour          (forecast_hour) int32 48B 1 2 3 4 5 6 7 8 9 10 11 12
  * latitude               (latitude) float64 6kB 90.0 89.75 ... -89.75 -90.0
  * longitude              (longitude) float64 12kB 0.0 0.25 0.5 ... 359.5 359.8
Data variables:
    E                      (forecast_initial_time, forecast_hour, latitude, longitude) float32 9GB dask.array<chunksize=(5, 12, 721, 1440), meta=np.ndarray>
Attributes:
    DATA_SOURCE:          ECMWF: https://cds.climate.copernicus.eu, Copernicu...
    NETCDF_CONVERSION:    CISL RDA: Conversion from ECMWF GRIB1 data to netCDF4.
    NETCDF_VERSION:       4.8.1
    CONVERSION_PLATFORM:  Linux r4i0n8 4.12.14-95.51-default #1 SMP Fri Apr 1...
    CONVERSION_DATE:      Fri Mar 17 12:52:09 MDT 2023
    Conventions:          CF-1.6
    NETCDF_COMPRESSION:   NCO: Precision-preserving compression to netCDF4/HD...
    history:              Fri Mar 17 12:52:18 2023: ncks -4 --ppc default=7 e...
    NCO:                  netCDF Operators version 5.0.3 (Homepage = http://n...